In [1]:
import pandas as pd
import sqlite3
import requests
import numpy as np
import folium
import folium.plugins 
import matplotlib.pyplot as plt

# Data for the RV grouping project

Online I found a complete list of camp grounds in CSV format from http://www.poi-factory.com/node/17657

I will now extract all the required information
- Latitude and Longitude Data
- Name of the Camp Site
- Save the data to a sql3 database for wasy retreival and querying

In [2]:
df_raw = pd.read_csv('ParksandCampsites.csv', header=None)

In [3]:
df_raw = df_raw.set_axis(['Longitude', 'Latitude', 'Campsite_Name','Address'], axis=1)
df_raw

Longitude   Latitude                                 Campsite_Name  \
0     -127.679933  55.249428           'KSAN Historical Village Campground   
1      -73.403468  44.030277               10 Acres Campground and RV Park   
2      -75.997158  44.276788                       1000 Islands Campground   
3      -76.054170  44.350050                   1000 Islands Camping Resort   
4      -76.216943  43.891877         1000 Islands/Association Island K O A   
...           ...        ...                                           ...   
17152  -94.849806  48.847923                                 Zippel Bay SP   
17153  -79.850677  35.603549                     Zooland Family Campground   
17154  -92.122085  44.301126               Zumbro Bottoms Horse Campground   
17155 -114.014515  35.224768                          Zuni Village RV Park   
17156 -115.653227  40.457238  Zunino/Jiggs Reservoir Recreation Area - BLM   

                                                 Address  
0                1450 River Rd,Haselton BC ,250 842-5940  
1      9 10 Acre Dr,Addison,*Vergennes VT *05491 ,802...  
2      42099 SR 12,Fishers Landing NY *13641 ,315 686...  
3      382 1000 Islands Pkwy,Lansdowne,*South Leeds a...  
4      15530 Snowshoe Rd,Henderson NY *13650 ,315 955...  
...                                                  ...  
17152              54th Ave NW,Williams MN ,218 783-6252  
17153  3671 Pisgah Covered Bridge Rd,Asheboro NC ,336...  
17154                       T-70,Kellog MN ,651 345-3401  
17155           2840 Airway Ave,Kingman AZ ,928 692-6202  
17156                       Rt 228,Elki NV ,775 753-0200  

[17157 rows x 4 columns]

In [4]:
con = sqlite3.connect('Campsite_data_4k.db')
df_raw.to_sql('Sites',con)
con.close()

In [5]:
con = sqlite3.connect('Campsite_data_4k.db')
query = ''' SELECT Campsite_Name, Latitude, Longitude FROM Sites WHERE Campsite_Name like '%RV%' AND Campsite_Name not like '%closed%'   '''
df_RV = pd.read_sql_query(query,con).set_index('Campsite_Name').drop_duplicates()
con.close
df_RV


Latitude   Longitude
Campsite_Name                                                      
10 Acres Campground and RV Park               44.030277  -73.403468
1015 RV Park                                  26.145834  -97.958195
11 Bridges Campground and RV Park             51.415188 -112.632344
115 Creek Rest Area (no services)             58.716979 -124.912576
1202 Motor Inn and RV Park                    62.387044 -140.873463
...                                                 ...         ...
Zion RV and Campground                        37.236637 -112.856060
Zion West RV Park                             37.231969 -113.364556
Zion's Gate RV Resort                         37.170192 -113.373832
Zuni Village RV Park                          35.224768 -114.014515
Zunino/Jiggs Reservoir Recreation Area - BLM  40.457238 -115.653227

[5311 rows x 2 columns]

## Map with the location Data

In [6]:
# create map of RV parks using latitude and longitude values
latitude = df_RV['Latitude'].mean()
longitude = df_RV['Longitude'].mean()
map_national_RV_parks = folium.Map(location=[latitude, longitude], zoom_start=4)

# add markers to map
marker_cluster = folium.plugins.MarkerCluster().add_to(map_national_RV_parks)
for lat, lng, name in zip(df_RV['Latitude'], df_RV['Longitude'], df_RV.reset_index()['Campsite_Name']):
    label = "<a  target='_blank' href='https://www.google.com/search?q={}'>{}</a>".format(name.replace(' ','%20'),name)
    #label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(marker_cluster)  

map_national_RV_parks

In [7]:
map_national_RV_parks.save('RV_Parks_Map.html')

In [8]:
CLIENT_ID = '24XQ2KIMXRYFZEWHRQZ1TSNKKDPFSLILAR1QNI1XPZREE5IF' # your Foursquare ID
CLIENT_SECRET = '4USSMOW03WWKLQEU5RWGMFPD3RSTDCNUS2KUUB0HEYUMAJGT' # your Foursquare Secret
ACCESS_TOKEN = 'BC2RNYUFSVGTBESYEFA1BZHJ1LMEBA5TXOZ1U2ZAJWXTRZZ1' # your FourSquare Access Token
VERSION = '20180604'
LIMIT = 60
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 24XQ2KIMXRYFZEWHRQZ1TSNKKDPFSLILAR1QNI1XPZREE5IF
CLIENT_SECRET:4USSMOW03WWKLQEU5RWGMFPD3RSTDCNUS2KUUB0HEYUMAJGT


## Neighboring venues data

Now I will use Foursquare to download neighboring venue data and save them to my sql3 database

In [ ]:
try:
    con = sqlite3.connect('Campsite_data_4k.db')
    query = ''' SELECT distinct(Campsite_Name) FROM Venues'''
    completed_venues = pd.read_sql_query(query,con)['Campsite_Name'].tolist()
    con.close
except:
    completed_venues = []
    
print('Number of completed venues that will not be run again: {}'.format(len(completed_venues)))
for key, item in df_RV.reset_index().iterrows():
    venues_list = []
    
    # create the API request URL
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        item['Latitude'], 
        item['Longitude'], 
        4000, #radius
        LIMIT)
    
    if not (item['Campsite_Name'] in completed_venues):
        print('New Site: {}'.format(item['Campsite_Name']))
        try:
            results = requests.get(url).json()["response"]['groups'][0]['items']
            for v in results:
                temp = {}
                temp['Campsite_Name']= item['Campsite_Name']
                temp['Latitude']= item['Latitude']
                temp['Longitude']= item['Longitude']
                temp['Venue']=v['venue']['name']
                temp['Venue_Latitude']=v['venue']['location']['lat']
                temp['Venue_Longitude']=v['venue']['location']['lng']  
                temp['Venue_Category']=v['venue']['categories'][0]['name']
                venues_list.append(temp)

            nearby_venues = pd.DataFrame(venues_list)
            con = sqlite3.connect('Campsite_data_4k.db')
            nearby_venues.to_sql('Venues',con,if_exists='append')
            con.close()
        except:
            print('Failed')

## Check data integrity

In [10]:
con = sqlite3.connect('Campsite_data_4k.db')
query = ''' SELECT * FROM Venues'''
completed_venues = pd.read_sql_query(query,con).drop('index',axis=1)
completed_venues

Campsite_Name   Latitude   Longitude  \
0       10 Acres Campground and RV Park  44.030277  -73.403468   
1       10 Acres Campground and RV Park  44.030277  -73.403468   
2       10 Acres Campground and RV Park  44.030277  -73.403468   
3       10 Acres Campground and RV Park  44.030277  -73.403468   
4       10 Acres Campground and RV Park  44.030277  -73.403468   
...                                 ...        ...         ...   
112138               Uvas Pines RV Park  37.060914 -121.671621   
112139               Uvas Pines RV Park  37.060914 -121.671621   
112140               Uvas Pines RV Park  37.060914 -121.671621   
112141               Uvas Pines RV Park  37.060914 -121.671621   
112142               Uvas Pines RV Park  37.060914 -121.671621   

                                  Venue  Venue_Latitude  Venue_Longitude  \
0                 The Bridge Restaurant       44.036137       -73.417700   
1                     Goodies Snack Bar       44.063204       -73.407221   
2            West Addison General Store       44.064368       -73.406900   
3       Crown Point State Historic Site       44.028508       -73.426759   
4                    vermont state line       44.038960       -73.416425   
...                                 ...             ...              ...   
112138                     One Iron Bar       37.067487      -121.632903   
112139          Frys.com Practice Range       37.068448      -121.632814   
112140          Sense Spa at CordeValle       37.067698      -121.632558   
112141      Frys.com Open Putting Green       37.067223      -121.631783   
112142             Chitactac Adams Park       37.030574      -121.656519   

             Venue_Category  
0       American Restaurant  
1               Snack Place  
2         Convenience Store  
3             Historic Site  
4           Border Crossing  
...                     ...  
112138           Restaurant  
112139          Golf Course  
112140                  Spa  
112141          Golf Course  
112142                 Park  

[112143 rows x 7 columns]

## Prepare the data for analysis

In [11]:
completed_venues.groupby('Campsite_Name').count()

Latitude  Longitude  \
Campsite_Name                                                             
10 Acres Campground and RV Park                            8          8   
1015 RV Park                                              48         48   
11 Bridges Campground and RV Park                          6          6   
1202 Motor Inn and RV Park                                 3          3   
1776 RV and Campground                                     5          5   
...                                                      ...        ...   
Upper Thames River Conservation Authority - Pit...        20         20   
Upper Thames River Conservation Authority - Wil...         4          4   
Upriver RV Resort                                         31         31   
Ute Creek RV Park and Campground                           5          5   
Uvas Pines RV Park                                        13         13   

                                                    Venue  Venue_Latitude  \
Campsite_Name                                                               
10 Acres Campground and RV Park                         8               8   
1015 RV Park                                           48              48   
11 Bridges Campground and RV Park                       6               6   
1202 Motor Inn and RV Park                              3               3   
1776 RV and Campground                                  5               5   
...                                                   ...             ...   
Upper Thames River Conservation Authority - Pit...     20              20   
Upper Thames River Conservation Authority - Wil...      4               4   
Upriver RV Resort                                      31              31   
Ute Creek RV Park and Campground                        5               5   
Uvas Pines RV Park                                     13              13   

                                                    Venue_Longitude  \
Campsite_Name                                                         
10 Acres Campground and RV Park                                   8   
1015 RV Park                                                     48   
11 Bridges Campground and RV Park                                 6   
1202 Motor Inn and RV Park                                        3   
1776 RV and Campground                                            5   
...                                                             ...   
Upper Thames River Conservation Authority - Pit...               20   
Upper Thames River Conservation Authority - Wil...                4   
Upriver RV Resort                                                31   
Ute Creek RV Park and Campground                                  5   
Uvas Pines RV Park                                               13   

                                                    Venue_Category  
Campsite_Name                                                       
10 Acres Campground and RV Park                                  8  
1015 RV Park                                                    48  
11 Bridges Campground and RV Park                                6  
1202 Motor Inn and RV Park                                       3  
1776 RV and Campground                                           5  
...                                                            ...  
Upper Thames River Conservation Authority - Pit...              20  
Upper Thames River Conservation Authority - Wil...               4  
Upriver RV Resort                                               31  
Ute Creek RV Park and Campground                                 5  
Uvas Pines RV Park                                              13  

[4608 rows x 6 columns]

In [12]:
completed_venues.groupby('Latitude').count()

Campsite_Name  Longitude  Venue  Venue_Latitude  Venue_Longitude  \
Latitude                                                                      
23.686356             11         11     11              11               11   
23.701440              9          9      9               9                9   
24.150010             60         60     60              60               60   
24.568251             45         45     45              45               45   
24.582099             12         12     12              12               12   
...                  ...        ...    ...             ...              ...   
64.832576              4          4      4               4                4   
64.835300             60         60     60              60               60   
64.839585             60         60     60              60               60   
64.962006              7          7      7               7                7   
66.372195              2          2      2               2                2   

           Venue_Category  
Latitude                   
23.686356              11  
23.701440               9  
24.150010              60  
24.568251              45  
24.582099              12  
...                   ...  
64.832576               4  
64.835300              60  
64.839585              60  
64.962006               7  
66.372195               2  

[4858 rows x 6 columns]

## We will need to group the camp sites by their lattitudes because of multiple sites that exist with the same name

In [13]:
# Let's look at the information regarding venues around the campsites
completed_venues.groupby('Latitude').count()['Venue_Category'].describe()

count    4858.000000
mean       23.084191
std        21.327831
min         1.000000
25%         5.000000
50%        13.000000
75%        40.000000
max       120.000000
Name: Venue_Category, dtype: float64

In [14]:
print('There are {} unique categories.'.format(len(completed_venues['Venue_Category'].unique())))

There are 593 unique categories.


In [15]:
# Let's generate a dataframe with dummy variables for all the venue types

Camp_sites_onehot = pd.get_dummies(completed_venues[['Venue_Category']], prefix="", prefix_sep="")
Camp_sites_onehot

ATM  Accessories Store  Adult Boutique  Advertising Agency  \
0         0                  0               0                   0   
1         0                  0               0                   0   
2         0                  0               0                   0   
3         0                  0               0                   0   
4         0                  0               0                   0   
...     ...                ...             ...                 ...   
112138    0                  0               0                   0   
112139    0                  0               0                   0   
112140    0                  0               0                   0   
112141    0                  0               0                   0   
112142    0                  0               0                   0   

        Afghan Restaurant  African Restaurant  Airfield  Airport  \
0                       0                   0         0        0   
1                       0                   0         0        0   
2                       0                   0         0        0   
3                       0                   0         0        0   
4                       0                   0         0        0   
...                   ...                 ...       ...      ...   
112138                  0                   0         0        0   
112139                  0                   0         0        0   
112140                  0                   0         0        0   
112141                  0                   0         0        0   
112142                  0                   0         0        0   

        Airport Food Court  Airport Gate  ...  Weight Loss Center  Whisky Bar  \
0                        0             0  ...                   0           0   
1                        0             0  ...                   0           0   
2                        0             0  ...                   0           0   
3                        0             0  ...                   0           0   
4                        0             0  ...                   0           0   
...                    ...           ...  ...                 ...         ...   
112138                   0             0  ...                   0           0   
112139                   0             0  ...                   0           0   
112140                   0             0  ...                   0           0   
112141                   0             0  ...                   0           0   
112142                   0             0  ...                   0           0   

        Wine Bar  Wine Shop  Winery  Wings Joint  Women's Store  Yoga Studio  \
0              0          0       0            0              0            0   
1              0          0       0            0              0            0   
2              0          0       0            0              0            0   
3              0          0       0            0              0            0   
4              0          0       0            0              0            0   
...          ...        ...     ...          ...            ...          ...   
112138         0          0       0            0              0            0   
112139         0          0       0            0              0            0   
112140         0          0       0            0              0            0   
112141         0          0       0            0              0            0   
112142         0          0       0            0              0            0   

        Zoo  Zoo Exhibit  
0         0            0  
1         0            0  
2         0            0  
3         0            0  
4         0            0  
...     ...          ...  
112138    0            0  
112139    0            0  
112140    0            0  
112141    0            0  
112142    0            0  

[112143 rows x 593 columns]

In [16]:
Camp_sites_onehot['Latitude'] = completed_venues['Latitude']
Camp_sites_onehot = Camp_sites_onehot[[Camp_sites_onehot.columns[-1]] + list(Camp_sites_onehot.columns[:-1])]

In [17]:
Camp_sites_onehot

Latitude  ATM  Accessories Store  Adult Boutique  Advertising Agency  \
0       44.030277    0                  0               0                   0   
1       44.030277    0                  0               0                   0   
2       44.030277    0                  0               0                   0   
3       44.030277    0                  0               0                   0   
4       44.030277    0                  0               0                   0   
...           ...  ...                ...             ...                 ...   
112138  37.060914    0                  0               0                   0   
112139  37.060914    0                  0               0                   0   
112140  37.060914    0                  0               0                   0   
112141  37.060914    0                  0               0                   0   
112142  37.060914    0                  0               0                   0   

        Afghan Restaurant  African Restaurant  Airfield  Airport  \
0                       0                   0         0        0   
1                       0                   0         0        0   
2                       0                   0         0        0   
3                       0                   0         0        0   
4                       0                   0         0        0   
...                   ...                 ...       ...      ...   
112138                  0                   0         0        0   
112139                  0                   0         0        0   
112140                  0                   0         0        0   
112141                  0                   0         0        0   
112142                  0                   0         0        0   

        Airport Food Court  ...  Weight Loss Center  Whisky Bar  Wine Bar  \
0                        0  ...                   0           0         0   
1                        0  ...                   0           0         0   
2                        0  ...                   0           0         0   
3                        0  ...                   0           0         0   
4                        0  ...                   0           0         0   
...                    ...  ...                 ...         ...       ...   
112138                   0  ...                   0           0         0   
112139                   0  ...                   0           0         0   
112140                   0  ...                   0           0         0   
112141                   0  ...                   0           0         0   
112142                   0  ...                   0           0         0   

        Wine Shop  Winery  Wings Joint  Women's Store  Yoga Studio  Zoo  \
0               0       0            0              0            0    0   
1               0       0            0              0            0    0   
2               0       0            0              0            0    0   
3               0       0            0              0            0    0   
4               0       0            0              0            0    0   
...           ...     ...          ...            ...          ...  ...   
112138          0       0            0              0            0    0   
112139          0       0            0              0            0    0   
112140          0       0            0              0            0    0   
112141          0       0            0              0            0    0   
112142          0       0            0              0            0    0   

        Zoo Exhibit  
0                 0  
1                 0  
2                 0  
3                 0  
4                 0  
...             ...  
112138            0  
112139            0  
112140            0  
112141            0  
112142            0  

[112143 rows x 594 columns]

In [18]:
campsite_grouped = Camp_sites_onehot.groupby('Latitude').mean().reset_index()
campsite_grouped

Latitude  ATM  Accessories Store  Adult Boutique  Advertising Agency  \
0     23.686356  0.0                0.0             0.0                 0.0   
1     23.701440  0.0                0.0             0.0                 0.0   
2     24.150010  0.0                0.0             0.0                 0.0   
3     24.568251  0.0                0.0             0.0                 0.0   
4     24.582099  0.0                0.0             0.0                 0.0   
...         ...  ...                ...             ...                 ...   
4853  64.832576  0.0                0.0             0.0                 0.0   
4854  64.835300  0.0                0.0             0.0                 0.0   
4855  64.839585  0.0                0.0             0.0                 0.0   
4856  64.962006  0.0                0.0             0.0                 0.0   
4857  66.372195  0.0                0.0             0.0                 0.0   

      Afghan Restaurant  African Restaurant  Airfield  Airport  \
0                   0.0                 0.0       0.0      0.0   
1                   0.0                 0.0       0.0      0.0   
2                   0.0                 0.0       0.0      0.0   
3                   0.0                 0.0       0.0      0.0   
4                   0.0                 0.0       0.0      0.0   
...                 ...                 ...       ...      ...   
4853                0.0                 0.0       0.0      0.0   
4854                0.0                 0.0       0.0      0.0   
4855                0.0                 0.0       0.0      0.0   
4856                0.0                 0.0       0.0      0.0   
4857                0.0                 0.0       0.0      0.0   

      Airport Food Court  ...  Weight Loss Center  Whisky Bar  Wine Bar  \
0                    0.0  ...                 0.0         0.0       0.0   
1                    0.0  ...                 0.0         0.0       0.0   
2                    0.0  ...                 0.0         0.0       0.0   
3                    0.0  ...                 0.0         0.0       0.0   
4                    0.0  ...                 0.0         0.0       0.0   
...                  ...  ...                 ...         ...       ...   
4853                 0.0  ...                 0.0         0.0       0.0   
4854                 0.0  ...                 0.0         0.0       0.0   
4855                 0.0  ...                 0.0         0.0       0.0   
4856                 0.0  ...                 0.0         0.0       0.0   
4857                 0.0  ...                 0.0         0.0       0.0   

      Wine Shop  Winery  Wings Joint  Women's Store  Yoga Studio       Zoo  \
0           0.0     0.0          0.0            0.0          0.0  0.000000   
1           0.0     0.0          0.0            0.0          0.0  0.000000   
2           0.0     0.0          0.0            0.0          0.0  0.016667   
3           0.0     0.0          0.0            0.0          0.0  0.000000   
4           0.0     0.0          0.0            0.0          0.0  0.000000   
...         ...     ...          ...            ...          ...       ...   
4853        0.0     0.0          0.0            0.0          0.0  0.000000   
4854        0.0     0.0          0.0            0.0          0.0  0.000000   
4855        0.0     0.0          0.0            0.0          0.0  0.000000   
4856        0.0     0.0          0.0            0.0          0.0  0.000000   
4857        0.0     0.0          0.0            0.0          0.0  0.000000   

      Zoo Exhibit  
0             0.0  
1             0.0  
2             0.0  
3             0.0  
4             0.0  
...           ...  
4853          0.0  
4854          0.0  
4855          0.0  
4856          0.0  
4857          0.0  

[4858 rows x 594 columns]

In [19]:
campsite_grouped.describe()

Latitude          ATM  Accessories Store  Adult Boutique  \
count  4858.000000  4858.000000        4858.000000     4858.000000   
mean     38.213853     0.001430           0.000606        0.000224   
std       7.629570     0.013831           0.005916        0.006030   
min      23.686356     0.000000           0.000000        0.000000   
25%      32.668042     0.000000           0.000000        0.000000   
50%      36.690422     0.000000           0.000000        0.000000   
75%      43.377063     0.000000           0.000000        0.000000   
max      66.372195     0.500000           0.200000        0.333333   

       Advertising Agency  Afghan Restaurant  African Restaurant     Airfield  \
count         4858.000000        4858.000000         4858.000000  4858.000000   
mean             0.000286           0.000003            0.000049     0.000008   
std              0.014813           0.000239            0.001649     0.000376   
min              0.000000           0.000000            0.000000     0.000000   
25%              0.000000           0.000000            0.000000     0.000000   
50%              0.000000           0.000000            0.000000     0.000000   
75%              0.000000           0.000000            0.000000     0.000000   
max              1.000000           0.016667            0.076923     0.018868   

           Airport  Airport Food Court  ...  Weight Loss Center   Whisky Bar  \
count  4858.000000         4858.000000  ...         4858.000000  4858.000000   
mean      0.005667            0.000008  ...            0.000029     0.000157   
std       0.034297            0.000531  ...            0.000705     0.002968   
min       0.000000            0.000000  ...            0.000000     0.000000   
25%       0.000000            0.000000  ...            0.000000     0.000000   
50%       0.000000            0.000000  ...            0.000000     0.000000   
75%       0.000000            0.000000  ...            0.000000     0.000000   
max       1.000000            0.037037  ...            0.020000     0.100000   

          Wine Bar    Wine Shop       Winery  Wings Joint  Women's Store  \
count  4858.000000  4858.000000  4858.000000  4858.000000    4858.000000   
mean      0.000893     0.000575     0.000737     0.001469       0.000736   
std       0.008810     0.006453     0.008294     0.007220       0.006448   
min       0.000000     0.000000     0.000000     0.000000       0.000000   
25%       0.000000     0.000000     0.000000     0.000000       0.000000   
50%       0.000000     0.000000     0.000000     0.000000       0.000000   
75%       0.000000     0.000000     0.000000     0.000000       0.000000   
max       0.250000     0.200000     0.230769     0.250000       0.250000   

       Yoga Studio          Zoo  Zoo Exhibit  
count  4858.000000  4858.000000  4858.000000  
mean      0.000294     0.000735     0.000150  
std       0.005031     0.009295     0.003778  
min       0.000000     0.000000     0.000000  
25%       0.000000     0.000000     0.000000  
50%       0.000000     0.000000     0.000000  
75%       0.000000     0.000000     0.000000  
max       0.250000     0.250000     0.183333  

[8 rows x 594 columns]